In [1]:
link1 = 'http://people.brunel.ac.uk/~mastjjb/jeb/orlib/files/cap82.txt'
link2 = 'http://people.brunel.ac.uk/~mastjjb/jeb/orlib/files/cap113.txt'
import numpy as np
import gurobipy as gp
from gurobipy import GRB

In [2]:
# define function to download data
def load_data(url, filename):
    import urllib.request
    response = urllib.request.urlretrieve(url,filename)
    file = open(filename,'r')
    return file

In [3]:
file = load_data(link2, 'cap113.txt')
data = file.readlines()

In [4]:
[locations, customers] = [int(x) for x in data[0].split(' ')[1:-1]]
capacity = []
fixcost = []
for i in range(locations):
    [c, f] = [float(x) for x in data[i+1].split(' ')[1:-1]]
    capacity.append(c)
    fixcost.append(f)
demand = []
varcost = np.zeros((locations,customers))
for j in range(customers):
    demand.append(float(data[j*9 + (1+locations)].split(' ')[1]))
    v = list(np.concatenate([data[j*9 + (1+locations+t)].split(' ')[1:-1] for t in range(1,9)]))
    for i in range(locations):
        varcost[i,j] = float(v[i])
        
        
print(locations)
print(customers)
print(capacity)
print(fixcost)
print(demand)
print(varcost)

50
50
[5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0]
[17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 0.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0]
[146.0, 87.0, 672.0, 1337.0, 31.0, 559.0, 2370.0, 1089.0, 33.0, 32.0, 5495.0, 904.0, 1466.0, 143.0, 615.0, 564.0, 226.0, 3016.0, 253.0, 195.0, 38.

In [5]:
def subproblem(model, where):
    if where == GRB.Callback.MIPSOL:
        v_y = model.cbGetSolution(model._y)
        #print(v_y)
        LB = model.cbGetSolution(model._z)
        print('Current LB: ', LB, '\n')
        print(model.cbGet(GRB.Callback.MIPSOL_OBJBND))
        print(model.cbGet(GRB.Callback.MIPSOL_OBJBST))
        
        bsp = gp.Model("Subproblem") 
        x = {}
        for i in range(locations):
            for j in range(customers):
                x[i,j] = bsp.addVar(obj=varcost[i,j])
        
        #unserved demand
        s = {}
        add_cost = np.max(varcost)*2
        for j in range(customers):
            s[j] = bsp.addVar(obj = add_cost)
        
        demand_constr = {} 
        for j in range(customers):
            demand_constr[j] = bsp.addConstr(sum(x[i,j] for i in range(locations)) + s[j] >= demand[j])
        
        log_constr = {}
        for i in range(locations):
            log_constr[i] = bsp.addConstr(sum(x[i,j] for j in range(customers)) <= v_y[i]* bigM)
        
        cap_constr = {}
        for i in range(locations):
            cap_constr[i] = bsp.addConstr(sum(x[i,j] for j in range(customers)) <= capacity[i])
        
        bsp.optimize()

        
        
        #update ub and lb
        fc = 0
        for i in range(locations):
            if sum(round(x[i,j].x) for j in range(customers)) > 0:
                fc+=fixcost[i]
        
        if bsp.objVal + fc > LB:
            v = np.zeros(customers) #dual of demand constraints
            for j in range(customers):
                v[j] = demand_constr[j].pi #get dual value
            
            w = np.zeros(locations) #dual of capacity constraints
            for i in range(locations):
                w[i] = cap_constr[i].pi
            
            cm = np.zeros(locations) #coefficient of y in master problem
            for i in range(locations):
                cm[i] = fixcost[i]+ capacity[i] * w[i]
            

            model.cbLazy(model._z  >= sum(demand[j] * v[j] for j in range(customers)) +   
                         sum(cm[i] * model._y[i] for i in range(locations)))

        
        # save result of x from subproblem
        global transport
        for i in range(locations):
            for j in range(customers):
                transport[i,j] = x[i,j].x
        #print([transport[locations-1][j] for j in range(customers)])
        #print(bsp.objVal)

        bsp.dispose()
                       


In [ ]:
transport = np.zeros((locations, customers)) # to save result of x from subproblem
# Masterproblem
                     
m = gp.Model("Benders Masterproblem")

y = {}
z = m.addVar(obj=1)                                                                           
for i in range(locations):
    y[i] = m.addVar(vtype=GRB.BINARY)
    

m.Params.lazyConstraints = 1
m._y = y
m._z = z
m.Params.TimeLimit = 5400
m.optimize(subproblem)
    
    
print("Objective: " + str(m.objVal))

print("Solution:")
import pandas as pd
index = ['Source ' + str(x+1) for x in range(locations)]
columns = ['Customer ' + str(x+1) for x in range(customers)]

solution = pd.DataFrame(index=index, columns=columns+['y'])

for i in range(locations):
    for j in range(customers):
        solution.iloc[i,j] = transport[i,j]
    solution.iloc[i,customers] = y[i].x

print(solution)


Using license file C:\Users\hadao\gurobi.lic
Academic license - for non-commercial use only
Changed value of parameter lazyConstraints to 1
   Prev: 0  Min: 0  Max: 1  Default: 0
Changed value of parameter TimeLimit to 5400.0
   Prev: inf  Min: 0.0  Max: inf  Default: inf
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 0 rows, 51 columns and 0 nonzeros
Model fingerprint: 0x222d02f8
Variable types: 1 continuous, 50 integer (50 binary)
Coefficient statistics:
  Matrix range     [0e+00, 0e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [0e+00, 0e+00]
Current LB:  0.0 

-1e+100
0.0
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 2550 columns and 5050 nonzeros
Model fingerprint: 0x5a33d5c7
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 100 rows and 2550

Model fingerprint: 0x4d9bbe1e
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 25 rows and 1250 columns
Presolve time: 0.00s
Presolved: 75 rows, 1300 columns, 2550 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      57    3.1559723e+09   0.000000e+00   0.000000e+00      0s

Solved in 57 iterations and 0.01 seconds
Optimal objective  3.155972293e+09
H    0     0                    3.156392e+09 2.8383e+09  10.1%     -    0s
Current LB:  3003591105.275001 

2838325671.6211867
3003591105.275001
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 2550 columns and 5050 nonzeros
Model fingerprint: 0x05e8e4d7
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS rang


Solved in 56 iterations and 0.01 seconds
Optimal objective  3.103870680e+09
Current LB:  3072499471.4624977 

2838325671.6211867
3072499471.4624977
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 2550 columns and 5050 nonzeros
Model fingerprint: 0xb99c600c
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 20 rows and 1000 columns
Presolve time: 0.00s
Presolved: 80 rows, 1550 columns, 3050 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      55    3.0973475e+09   0.000000e+00   0.000000e+00      0s

Solved in 55 iterations and 0.01 seconds
Optimal objective  3.097347537e+09
Current LB:  3073796349.1000037 

2838325671.6211867
3073796349.1000037
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 255

Presolve removed 13 rows and 650 columns
Presolve time: 0.01s
Presolved: 87 rows, 1900 columns, 3750 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      60    3.3377335e+09   0.000000e+00   0.000000e+00      0s

Solved in 60 iterations and 0.01 seconds
Optimal objective  3.337733509e+09
Current LB:  2998671677.587503 

2947840844.3664293
2998671677.587503
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 2550 columns and 5050 nonzeros
Model fingerprint: 0xdc375706
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 12 rows and 600 columns
Presolve time: 0.01s
Presolved: 88 rows, 1950 columns, 3850 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
   

  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 11 rows and 550 columns
Presolve time: 0.01s
Presolved: 89 rows, 2000 columns, 3950 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      55    3.0851897e+09   0.000000e+00   0.000000e+00      0s

Solved in 55 iterations and 0.01 seconds
Optimal objective  3.085189660e+09
Current LB:  3074931092.524999 

2947840844.3664293
3074931092.524999
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 2550 columns and 5050 nonzeros
Model fingerprint: 0xb9358df4
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 10 rows and 500 columns
Presolve time: 0.00s
Presolved: 90 rows, 2050 columns, 4050 nonze

...

       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      55    3.0844631e+09   0.000000e+00   0.000000e+00      0s

Solved in 55 iterations and 0.01 seconds
Optimal objective  3.084463111e+09
Current LB:  3077856881.8000045 

3073692994.9147305
3077856881.8000045
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 2550 columns and 5050 nonzeros
Model fingerprint: 0xb54745d4
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 9 rows and 450 columns
Presolve time: 0.01s
Presolved: 91 rows, 2100 columns, 4150 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      55    3.0930963e+09   0.000000e+00   0.000000e+00      0s

Solved in 55 iterations and 0.02 seconds
Optimal objective  3.093096302e+09
Current LB:  3081461847.274994 

307

Presolve time: 0.01s
Presolved: 89 rows, 2000 columns, 3950 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      55    3.0946028e+09   0.000000e+00   0.000000e+00      0s

Solved in 55 iterations and 0.02 seconds
Optimal objective  3.094602779e+09
Current LB:  3081307058.087504 

3073693105.5818267
3081307058.087504
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 2550 columns and 5050 nonzeros
Model fingerprint: 0xcd62bd5f
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 13 rows and 650 columns
Presolve time: 0.01s
Presolved: 87 rows, 1900 columns, 3750 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      55    3.0920262e+09   0.000000e+00   0

  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 17 rows and 850 columns
Presolve time: 0.01s
Presolved: 83 rows, 1700 columns, 3350 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      55    3.0934963e+09   0.000000e+00   0.000000e+00      0s

Solved in 55 iterations and 0.01 seconds
Optimal objective  3.093496334e+09
Current LB:  3081791756.2625046 

3073693194.987056
3081791756.2625046
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 2550 columns and 5050 nonzeros
Model fingerprint: 0x9c9e09c1
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 17 rows and 850 columns
Presolve time: 0.01s
Presolved: 83 rows, 1700 columns, 3350 nonzeros

Iteration    Objective      

Model fingerprint: 0xee9ae230
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 11 rows and 550 columns
Presolve time: 0.01s
Presolved: 89 rows, 2000 columns, 3950 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      55    3.0903472e+09   0.000000e+00   0.000000e+00      0s

Solved in 55 iterations and 0.02 seconds
Optimal objective  3.090347198e+09
Current LB:  3081051489.258319 

3073694205.363786
3081051489.258319
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 2550 columns and 5050 nonzeros
Model fingerprint: 0x2ba3f6a3
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 12 rows and 600 columns
Presolve tim

Optimal objective  3.089769522e+09
Current LB:  3081305068.762504 

3073694273.1989045
3081305068.762504
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 2550 columns and 5050 nonzeros
Model fingerprint: 0xf9d8de78
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 3e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 14 rows and 700 columns
Presolve time: 0.01s
Presolved: 86 rows, 1850 columns, 3650 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      56    3.0919341e+09   0.000000e+00   0.000000e+00      0s

Solved in 56 iterations and 0.01 seconds
Optimal objective  3.091934147e+09
Current LB:  3081394385.599064 

3073694273.1989045
3081394385.599064
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 100 rows, 2550 columns and 5050 nonzeros
Model fingerprint: 

In [8]:
#Number of open warehouses
sum(y[i].x for i in y.keys())

50.0

In [ ]:
#resolve transportation problem with fixed y obtained from Benders

In [9]:
y0 = [y[i].x for i in y.keys()]

In [10]:
model0 = gp.Model()
x0 = {}
for i in range(locations):
    for j in range(customers):
        x0[i,j] = model0.addVar(obj=varcost[i][j])

#demand constraint
demand_constr = {} 
for j in range(customers):
    demand_constr[j] = model0.addConstr(sum(x0[i,j] for i in range(locations)) >= demand[j])
        
#capacity constraint
cap_constr = {}
for i in range(locations):
    cap_constr[i] = model0.addConstr(sum(x0[i,j] for j in range(customers)) <= capacity[i])

#logical constraint
log_constr = {}
for i in range(locations):
    log_constr[i] = model0.addConstr(sum(x0[i,j] for j in range(customers)) <= y0[i] * sum(demand))

model0.optimize()

print("Objective: " + str(model0.objVal))

print("Solution:")
import pandas as pd
index = ['Source ' + str(x+1) for x in range(locations)]
columns = ['Customer ' + str(x+1) for x in range(customers)]

solution = pd.DataFrame(index=index, columns=columns)

for i in range(locations):
    for j in range(customers):
        solution.iloc[i,j] = x0[i,j].x

print(solution)

Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0xfac42826
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [4e+02, 1e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 6e+04]
Presolve removed 50 rows and 0 columns
Presolve time: 0.01s
Presolved: 100 rows, 2500 columns, 5000 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      55    3.0791167e+09   0.000000e+00   0.000000e+00      0s

Solved in 55 iterations and 0.01 seconds
Optimal objective  3.079116664e+09
Objective: 3079116663.75
Solution:
          Customer 1 Customer 2 Customer 3 Customer 4 Customer 5 Customer 6  \
Source 1         146          0          0          0          0          0   
Source 2           0         87          0          0          0          0   
Source 3           0          0        67

[50 rows x 50 columns]


In [11]:
#Total cost including fixed and transportation cost
model0.objVal+sum([y0[i]*fixcost[i] for i in range(locations)])

3079974163.75

The optimal cost from Benders decompostion approach is the same as that from MILP.